This code was originally written as part of an experiment looking at an NDVI time series for pixels adjacent to EOD point data. The original script is located in PhD -> Projects -> BFAST Breakpoint Experiment. The script can be used to extract values from individual imagery (ex. Landsat 7) or a time series of imagery that has been converted using the .toBands() function (ex. Landsat 5).

In [1]:
import os
import ee
import geemap

In [2]:
Map = geemap.Map(center=[38, 72], zoom = 7)
Map

Map(center=[38, 72], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Tog…

In [3]:
#Bring in EOD callout data from local shapefile
in_shp = 'C:/Users/Jeremy/OneDrive - UBC/PhD/Data/Conflict/HALO Trust/HALO Trust Khenj Data/EOD Khenj Shapefile/EOD_khenj.shp'
EOD_ee = geemap.shp_to_ee(in_shp)
EOD_geometry = EOD_ee.geometry()

#Add aoi_geometry to the map
Map.addLayer(EOD_geometry, {}, 'EOD Callouts')

In [4]:
# #Filter the EOD dataset to extract just the point in Burya Bala village (task_68289919)
task_id_to_filter = 68289919

# Create a filter based on the 'task_id' field
filter_task_id = ee.Filter.eq('task_id', task_id_to_filter)

# Use the filter to check if the feature satisfies the condition
is_feature_matching = EOD_ee.filter(filter_task_id).size().getInfo() > 0

# Print the result
print("Does the feature match the filter condition?", is_feature_matching)

Does the feature match the filter condition? True


In [5]:
# Use the filter to get a feature collection with matching features
filtered_feature_collection = EOD_ee.filter(filter_task_id)

# Get the first feature from the filtered collection (there might be none)
filtered_feature = filtered_feature_collection.first()

# Check if a matching feature was found and print the information of the result
if filtered_feature is not None:
    print("Filtered Feature:", filtered_feature.getInfo())
else:
    print("No matching feature found.")

Filtered Feature: {'type': 'Feature', 'geometry': {'type': 'Point', 'coordinates': [69.83379000000008, 35.496710000000064]}, 'id': '14', 'properties': {'activity': 'EOD', 'asset_atta': '', 'asset_code': '', 'asset_type': '', 'contract_1': 10519, 'contract_i': 10519, 'contract_p': 'VTF SUR/EOD - HMA', 'coord_x': 69.83379, 'coord_y': 35.49671, 'cycle_mont': 'December 2012', 'date_from': None, 'date_to': None, 'district': 'Khenj (Hese- Awal)', 'donor_cont': 'VTF SUR/EOD', 'donor_name': 'VTF', 'end_date': '20121204', 'imas_class': 'Spot Task', 'latitude': 35.49671, 'longitude': 69.83379, 'method': 'EOD Call Out', 'month_acti': '20121221', 'project_id': 119, 'project_na': 'HMA', 'province': 'Panjsher', 'sop': 'EOD', 'start_date': '20121204', 'status': 'Completed', 'sub_method': 'EOD', 'task_code': 'ES/4191', 'task_id': 68289919, 'task_name': 'Borya Bala', 'task_prior': 'NA', 'task_type': 'EOD', 'team_code': 'Survey/EOD-04', 'village': 'Burya Bala', 'village_co': 'L48556', 'ward': 'Dashti Re

In [6]:
#Convert the filtered feature to a geometry and add it to the map in red
filtered_feature_geometry = filtered_feature.geometry()
Map.addLayer(filtered_feature_geometry, {'color': 'FF0000'}, 'Filtered Feature')
#Centre the map over the point of interest
Map.centerObject(filtered_feature_geometry, 18) # Zoom level 18

In [7]:
# Set up parameters for filtering the EE dataset

# Filter by bounds by aoi bounds, Khenj district
boundaries = ee.FeatureCollection('FAO/GAUL_SIMPLIFIED_500m/2015/level2') # Bring in global second level admin. divisions
aoi = boundaries.filter(ee.Filter.eq('ADM2_NAME', 'Khenj (Hes-e- Awal)')) # Filter the dataset based on the ADM2_NAME property
aoi_geometry = aoi.geometry()

# Define a time range for the Landsat image collection
start_date = '1999-01-01'
end_date = '2003-12-31'

In [8]:
# Set up Landsat 7 with NDVI for a single image extraction

# Filter the Landsat 7 image collection for the specified time range and region
landsat7_collection = ee.ImageCollection('LANDSAT/LE07/C01/T1_TOA') \
    .filterBounds(aoi_geometry) \
    .filterDate(ee.Date(start_date), ee.Date(end_date))

# Select the first image from the collection
landsat7 = ee.Image(landsat7_collection.first())

# Create NDVI function
def add_ndvi(image):
    ndvi = image.normalizedDifference(['B4', 'B3']).rename('ndvi')
    return image.addBands(ndvi)

# Apply NDVI function to Landsat 7 image
landsat7_with_ndvi = add_ndvi(landsat7)

# Add the Landsat 7 image with NDVI to the map
ndvi_params = {'min': -1, 'max': 1, 'palette': ['red', 'white', 'green']}
Map.addLayer(landsat7_with_ndvi.select(['ndvi']), ndvi_params, 'NDVI')

#Display the map
Map

Map(center=[35.49671000000006, 69.83379000000008], controls=(WidgetControl(options=['position', 'transparent_b…

In [41]:
# Set up Landsat 5 time series of NDVI

# Set Landsat parameters
months = list(range(1, 13))
years = list(range(1984, 2013))  # Adjusted to include 2012

# Function to create monthly composites
def create_monthly_composite(year, month):
    start_date = ee.Date.fromYMD(year, month, 1)
    end_date = start_date.advance(1, 'month')

    # Bring in USGS Landsat 5 Level 2, Collection 2, Tier 1 dataset
    dataset = (ee.ImageCollection('LANDSAT/LT05/C02/T1_L2')
               .filterDate(start_date, end_date)
               .filterBounds(aoi))

    # Scaling and masking
    def apply_mask_scale(image):
        qa_mask = image.select('QA_PIXEL').bitwiseAnd(ee.Number(2).pow(5)).eq(0)
        saturation_mask = image.select('QA_RADSAT').eq(0)
        # Applies scaling factors.
        optical_bands = image.select('SR_B.').multiply(0.0000275).add(-0.2)
        thermal_band = image.select('ST_B6').multiply(0.00341802).add(149.0)
        return (image.addBands(optical_bands, None, True)
                .addBands(thermal_band, None, True)
                .updateMask(qa_mask)
                .updateMask(saturation_mask))

    # Apply scaling and masking to the dataset
    #dataset = dataset.map(apply_mask_scale)

    # Create NDVI function
    def add_ndvi(image):
        ndvi = image.normalizedDifference(['SR_B4', 'SR_B3']).rename('ndvi')
        return image.addBands(ndvi)

    # Apply NDVI function
    dataset = dataset.map(add_ndvi)

    dataset = dataset.select('ndvi') # Filter just the ndvi bands before creating monthly composites

    # Take the median, clipping to aoi
    dataset = dataset.median().clip(aoi)

    return dataset.set('system:time_start', start_date)

In [42]:
# Create monthly composites for each month across all years
monthly_composites = (ee.ImageCollection.fromImages(
    [create_monthly_composite(year, month) for year in years for month in months]))

# Print the resulting ImageCollection
print(monthly_composites)

ee.ImageCollection({
  "functionInvocationValue": {
    "functionName": "ImageCollection.fromImages",
    "arguments": {
      "images": {
        "arrayValue": {
          "values": [
            {
              "functionInvocationValue": {
                "functionName": "Element.set",
                "arguments": {
                  "key": {
                    "constantValue": "system:time_start"
                  },
                  "object": {
                    "functionInvocationValue": {
                      "functionName": "Image.clip",
                      "arguments": {
                        "geometry": {
                          "functionInvocationValue": {
                            "functionName": "Collection.filter",
                            "arguments": {
                              "collection": {
                                "functionInvocationValue": {
                                  "functionName": "Collection.loadTable",
                         

In [43]:
# Convert the image collection to an image
monthly_composites_bands = monthly_composites.toBands() # This step essentially takes the time series of data and converts it to a single image with multiple bands
monthly_composites_bands.getInfo() # Check that the data is valid

{'type': 'Image',
 'bands': [{'id': '26_ndvi',
   'data_type': {'type': 'PixelType',
    'precision': 'float',
    'min': -1,
    'max': 1},
   'crs': 'EPSG:4326',
   'crs_transform': [1, 0, 0, 0, 1, 0]},
  {'id': '33_ndvi',
   'data_type': {'type': 'PixelType',
    'precision': 'float',
    'min': -1,
    'max': 1},
   'crs': 'EPSG:4326',
   'crs_transform': [1, 0, 0, 0, 1, 0]},
  {'id': '46_ndvi',
   'data_type': {'type': 'PixelType',
    'precision': 'float',
    'min': -1,
    'max': 1},
   'crs': 'EPSG:4326',
   'crs_transform': [1, 0, 0, 0, 1, 0]},
  {'id': '47_ndvi',
   'data_type': {'type': 'PixelType',
    'precision': 'float',
    'min': -1,
    'max': 1},
   'crs': 'EPSG:4326',
   'crs_transform': [1, 0, 0, 0, 1, 0]},
  {'id': '48_ndvi',
   'data_type': {'type': 'PixelType',
    'precision': 'float',
    'min': -1,
    'max': 1},
   'crs': 'EPSG:4326',
   'crs_transform': [1, 0, 0, 0, 1, 0]},
  {'id': '50_ndvi',
   'data_type': {'type': 'PixelType',
    'precision': 'float',

In [44]:
# Set parameters for exporting values from Landsat NDVI to CSV
work_dir = os.path.expanduser('C:/Users/Jeremy/OneDrive - UBC/PhD/Projects/BFAST Breakpoint Experiment/Outputs')
out_csv = os.path.join(work_dir, 'landsat.csv')
in_fc = filtered_feature_collection

In [47]:
# Export Landsat pixel values to CSV
geemap.extract_values_to_points(in_fc, 
                                monthly_composites_bands, 
                                out_csv,
                                scale=30) # Inlucde scale in meters to prevent the error "Specify a scale or crs & crs_transform"

Generating URL ...
Please wait ...
Data downloaded to C:\Users\Jeremy\OneDrive - UBC\PhD\Projects\BFAST Breakpoint Experiment\Outputs\landsat.csv
